In [28]:

from openai import OpenAI
import os
from dotenv import load_dotenv
import pandas as pd

In [ ]:
load_dotenv('./.env')

In [88]:
books_dir = 'data'
documents = []
for filename in os.listdir(books_dir):
    if filename.endswith('.txt'):
        with open(os.path.join(books_dir, filename), 'r', encoding='utf-8') as file:
            text = file.read()
            documents.append(text)

print(f"Загружено {len(documents)} книг.")

Загружено 7 книг.


In [42]:
BOOK_NAMES = {
    1: 'Гарри Поттер и философский камень',
    2: 'Гарри Поттер и тайная комната',
    3: 'Гарри Поттер и узник Азкабана',
    4: 'Гарри Поттер и кубок огня',
    5: 'Гарри Поттер и орден феникса',
    6: 'Гарри Поттер и принц-полукровка',
    7: 'Гарри Поттер и дары смерти',
}

In [89]:
import re

def get_part_name(part):
    result = re.search(r'\d+\n+\s*(.*?)\n+', part, re.DOTALL)
    if result:
        extracted_text = result.group(1).strip()
        return extracted_text

In [90]:
books_and_parts = {}
book_num = 0
for book in documents:
    book_num += 1
    parts = book.split('Глава ')
    book_parts = {}
    for num_part in range(1, len(parts)):
        book_parts = book_parts | {
            num_part: (get_part_name(parts[num_part]), parts[num_part])
        }    
    books_and_parts = books_and_parts | {book_num: book_parts}

In [91]:
books_and_parts

{1: {1: ('МАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ',
   '1\n\nМАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ\n\n\n\nМистер и миссис Дурсли проживали в доме номер четыре по Тисовой улице и всегда с гордостью заявляли, что они, к счастью, абсолютно нормальные люди. Уж от кого-кого, а от них никак нельзя было ожидать, чтобы они попали в какую-нибудь странную или загадочную историю. Мистер и миссис Дурсли весьма неодобрительно относились к любым странностям, загадкам и прочей ерунде.\n\n\n\n\n\nМистер Дурсль возглавлял фирму под названием «Граннингс», которая специализировалась на производстве дрелей. Это был полный мужчина с очень пышными усами и очень короткой шеей. Что же касается миссис Дурсль, она была тощей блондинкой с шеей почти вдвое длиннее, чем положено при ее росте. Однако этот недостаток пришелся ей весьма кстати, поскольку большую часть времени миссис Дурсль следила за соседями и подслушивала их разговоры. А с такой шеей, как у нее, было очень удобно заглядывать за чужие заборы. У мистера и миссис Дурслей был маленьк

In [100]:
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_core.documents import Document

docs = []

text_splitter = RecursiveCharacterTextSplitter(
    separators=['\n\n\n\n', '\n', '\n\n', "", " "],
    chunk_size=4000,
    chunk_overlap=500,
    length_function=len,
    is_separator_regex=False,
)

for book_num, parts in books_and_parts.items():
    for part_num, part in parts.items():
        texts = text_splitter.split_text(part[1])
        metadata = {
            'Номер книги': book_num,
            'Название книги': BOOK_NAMES[book_num],
            'Номер главы': part_num,
            'Название главы': part[0]
        }
        if part[0] is None:
            print(metadata)
        for text_part in texts:
            if len(text_part) < 300:
                continue
            docs.append(Document(page_content=f"{part[0]}\n{text_part}\n", metadata=metadata))


In [101]:
docs

[Document(metadata={'Номер книги': 1, 'Название книги': 'Гарри Поттер и философский камень', 'Номер главы': 1, 'Название главы': 'МАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ'}, page_content='МАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ\n1\n\nМАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ\n\n\n\nМистер и миссис Дурсли проживали в доме номер четыре по Тисовой улице и всегда с гордостью заявляли, что они, к счастью, абсолютно нормальные люди. Уж от кого-кого, а от них никак нельзя было ожидать, чтобы они попали в какую-нибудь странную или загадочную историю. Мистер и миссис Дурсли весьма неодобрительно относились к любым странностям, загадкам и прочей ерунде.\n'),
 Document(metadata={'Номер книги': 1, 'Название книги': 'Гарри Поттер и философский камень', 'Номер главы': 1, 'Название главы': 'МАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ'}, page_content='МАЛЬЧИК, КОТОРЫЙ ВЫЖИЛ\nМистер Дурсль возглавлял фирму под названием «Граннингс», которая специализировалась на производстве дрелей. Это был полный мужчина с очень пышными усами и очень короткой шеей. Что же касается миссис Дур

In [102]:
import faiss
from langchain.vectorstores import FAISS
from langchain_community.docstore.in_memory import InMemoryDocstore
from langchain.embeddings import HuggingFaceEmbeddings


model = HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')
index = faiss.IndexFlatL2(len(model.embed_query('hello world')))

vectorstore = FAISS(
    embedding_function=model,
    index=index,
    docstore=InMemoryDocstore(),
    index_to_docstore_id={},
    distance_strategy='cosine'
)

vectorstore.add_documents(documents=docs)

['9168d74d-e286-4492-9385-8d0b8f9ea0bb',
 '8ed53241-7711-4d96-b5f6-cfb31a98ffa7',
 '3f58731c-7b83-456d-a5fa-4c707575195a',
 '50ab7b55-0078-414c-9cdc-a367bf599f4b',
 'dac3088b-4acb-486d-8f71-2556487555fa',
 'ab9ac9fb-9d74-41dd-bb07-ec88a3899a63',
 'dbc53448-cb85-408f-9a9e-9f3e8e68e254',
 '18de86ae-07a1-4d41-9635-48dd230f32d5',
 '881729b1-862f-4745-b09c-d8a8c8b38a06',
 '15fbc65c-d85f-41ab-aba7-c61e7a531028',
 'fb61451a-01ea-4bee-97c3-eeb313e2743d',
 '2c5b3e35-4955-4411-b534-1faca549974a',
 '2ec15950-72ab-491c-b6ae-3fc081f3ccd4',
 '968eed11-ad60-48e3-83dd-cdb04b2e08b6',
 'ccceb3e0-7e71-4a54-b286-7fc045004717',
 '7983cc91-6cca-4623-a437-87c3fe9daa55',
 '3332d86e-aa05-49dc-a727-a512b6099995',
 'fc1e0827-1928-49d6-b4ea-6b070469bd0c',
 '234d3fec-82d2-4690-b3f5-18679cde465c',
 'ebbaaeec-218d-4207-8199-78b9b5f32929',
 '91814078-ee49-4cbc-9fc7-5ea55c2e8a5f',
 '97db689e-f0e1-441d-9a73-0ff6cfd93b6d',
 '6c23bc6b-9c33-4a27-aee4-4a93ee3c348d',
 '48c74054-a0a3-4338-99af-ec6e9406f2af',
 '22f2de52-f45f-

In [103]:
vectorstore.save_local('HP_vector_store')

In [116]:
client = OpenAI(
    api_key=os.getenv("API_KEY"),
    base_url=os.getenv("API_URL")
)

sys_prompt = f'''
Ты часть RAG системы по поиску информации по книгам о Гарри Поттере.\n
Пользователь задает вопросы по сюжету/персонажам книги, ты предоставляешь ответ на основе базы знаний по книге, с указанием глав/частей книги, на основе которых был сформирован ответ.\n
Информация о частях книги тебе будет подаваться RAG составляющей, не забудь ее упомянуть при ответе.\n
Перед ответом проверяй себя - из-за неверных твоих ответов пользователь может не выжить, ты же не хочешь, чтобы кто-то из-за тебя умер.\n
'''

In [117]:
def answer(prompt):
    retriever = vectorstore.as_retriever()
    retr_res = retriever.invoke(prompt, k=3)
    response = client.chat.completions.create(
        model=os.getenv('model'),
        messages=[
            {
                "role": "user", 
                "content": f'''
                {sys_prompt}]\n
                'Запрос пользователя: {prompt}\n
                'Результаты rag: {"".join(res.page_content for res in retr_res)}
                'Использованные части: {"".join(str(res.metadata) for res in retr_res)}
                            '''
            }
        ]
    )
    return response.choices[0].message.content

In [119]:
answer('Сколько лет было гарри поттеру в 5 книге')

'В пятой книге, "Гарри Поттер и Орден феникса", Гарри Поттеру было 15 лет. Это можно подтвердить разделами, в которых говорится о его возрасте. \n\n### Использованные части:\n- **Книга:** Гарри Поттер и Орден феникса\n- **Глава:** 26, "Секреты из прошлого" (не указана в предоставленных данных, но это тот раздел, где обсуждается его возраст)\n\nЕсли требуется больше информации или детали, дайте знать!'